# Data Augmentation

## 1. Back-translation:

"In a recent Kaggle competition (Jigsaw Toxic Comment Classification) a really neat regularization strategy was used, which ended up being a big factor in the First Place Winner’s solution.

The idea was to create augmented text data by translating it into some foreign language, and then translating it back to English.

The performance gain was huge.

Presumably, Google Translate would make errors in the translation processes, which helped prevent the RNNs from overfitting to irrelevant features." (Quora)

* Install mtranslate API for Google Translate:

a). Clone the repository and use setup: https://github.com/mouuff/mtranslate

or

b). Use pip: pip install mtranslate==1.3 

* Basic usage of mtranslate:

In [5]:
from mtranslate import translate

def main():
    to_translate = 'Bonjour comment allez vous?'
    print(translate(to_translate)) # english output
    print(translate(to_translate, 'en')) # define output languages
    print(translate(to_translate, 'ru')) # define output languages
    print(translate(to_translate, 'fr')) # define output languages
if __name__ == '__main__':
    main()

Hello how are you?
Hello how are you?
Привет, как дела?
Bonjour comment allez vous?


* Back-translation example:

In [23]:
from mtranslate import translate

def main():
    to_translate = "I have seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated."
    print("- Original english: \n", to_translate)
    german_translation = translate(to_translate, 'de')
    print("\n- German: \n", german_translation)
    en_translation = translate(german_translation)
    print("\n- English (new data): \n", en_translation)
if __name__ == '__main__':
    main()

- Original english: 
 I have seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated.

- German: 
 Ich habe einige Datenerhöhungstechniken für Bilddaten gesehen. Es wurde jedoch nicht viel Arbeit online zu Datenerweiterungstechniken für Textdaten gefunden. Irgendwelche Vorschläge diesbezüglich werden geschätzt.

- English (new data): 
 I have seen some data enhancement techniques for image data. However, not much work has been done online on text data extension techniques. Any suggestions in this regard are appreciated.


# 2. Thesarius (with WordNet):

In [25]:
import nltk
from nltk.corpus import wordnet as wn

our_input = "I have seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated."
def thesarius(our_input):
    translation = ""
    punctuation = [".",",","?","!",":",";","...","\"","\'","\'\''","(",")","[","]","{","}"]
    for word in our_input.split(" "):
        clean_word = ""
        for el in word:
            if el not in punctuation:
                clean_word+=el
        synon = wn.synsets(clean_word)
        alle = []
        for el in synon:
            a = el.lemma_names()
            alle.append(a[0])
        if len(alle) > 0:
            a = alle[0]
            if a.split("_"):
                x = ""
                a = a.split("_")
                for el in a:
                    x+=el
                    x+=" "
                x.strip()
                a = x
            translation+=a
            translation+=" "
        else:
            translation+=clean_word 
            translation+=" "
    if translation != our_input: 
        return translation
    print("- Our data:\n", our_input)
    print("\n- New data:\n", translation)
    
if __name__ == "__main__":
    thesarius(our_input)



New Version of Thesaurus (with geometrical distribution):

In [218]:
import os
def geom_distribution(i):
        # Create a geometrical distribution for i given words:
    p = 0.5 # parameter
    geom = []
    for el in range(i):
        probability = p**(el+1)  
        geom.append(probability)
    #print("geom",geom)    
    # normalize:
    sum_geom = 0
    for el in geom:
        sum_geom+=el 
    #print("sum geom",sum_geom)
    for e in range(len(geom)):
        geom[e] = geom[e]/sum_geom
    #print("norm geom distr: ", geom) # normalized geometrical distribution
    
    # Generate a random number between [0,1]
    if i > 1: # there are more than 1 word to replace
        #num = random.randrange(1)
        x = int.from_bytes(os.urandom(8), byteorder="big") / ((1 << 64) - 1) # generate a random number 
    elif i ==1: # there is only one word to replace
        x = 0
    else: # if = 0 -- there are no words to replace
        return None
    #print("x: ", x)
    
    # Calculate a cumulative sum:
    cum_sum = []
    for el in range(len(geom)):
        #print(el)
        if el >0:
            cum_sum.append(geom[el]+cum_sum[el-1])
        else:
            cum_sum.append(geom[el])
        #print(cum_sum)    
    #print("cum_sum",cum_sum)
    # calculate t - number of the words to replace
    if len(cum_sum) == 1:
        t = 1
        return t
    for i in range(len(cum_sum)-1):
        #print("i",i)
        if x < cum_sum[i]:
            #print(x,cum_sum[i])
            t = i+1            
            return t
            break
        else:
            t = len(cum_sum)
    return t

In [212]:
import nltk
#import random
from nltk.stem.lancaster import LancasterStemmer
lancaster_stemmer = LancasterStemmer()
import os

from nltk.corpus import wordnet as wn
our_input = "I have seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated."
#our_input = "jfd went my man good bad expelent"
def thesaurus_right(our_input):
    clean_input = [] # the words that could be replaced
    pos_for_thesaurus = ["JJ","JJR","JJS","NN","RB","RBR","RBS","VB","VBD","VBG","VBN","VBP","VBZ"]
    translation = ""
    punctuation = [".",",","?","!",":",";","...","\"","\'","\'\''","(",")","[","]","{","}"]
    # Clean the words from punctuation. Choose the words that could be replaced (Nouns, Adverbs, Verbs, Adjectives)
    for index in range(len(our_input.split(" "))):
        clean_word = ""
        for el in our_input.split(" ")[index]:
            if el not in punctuation:
                clean_word+=el
        try:
            te = nltk.word_tokenize(clean_word)
            x = nltk.pos_tag(te)
            
            if x[0][1] in pos_for_thesaurus:
                x = (x,index)
                clean_input.append(x)
        except:
            continue
    # check if there are synonyms in thesaurus:  
    new_clean_input = []
    for w in clean_input: 
        try: 
            synon = wn.synsets(wn.morphy(w[0][0][0]))
            if synon !=[]:
                new_clean_input.append(w)

        except:
            synon = wn.synsets(w[0][0][0])
            if synon !=[]:
                new_clean_input.append(w)

        else:
            synon = None
 
                               
    i = len(new_clean_input)

    geom_d = geom_distribution(i)
 
    if type(geom_d)==int:
        pass
    else:
        return our_input
        

    count = 0
    num = 0
    
    print("Number of words to replace: ", geom_d)
    for wo_to_replace in range(geom_d):
        new_a = []
        alle = []

        while len(new_a)==0: # if we don't find the synonym in thesarius, we go to the next word to replace
            #print(len(new_a))
            if num < len(new_clean_input):
                #print("hh")
                w_to_replace = new_clean_input[num][0]

                try: 
                    synon = wn.synsets(wn.morphy(w_to_replace[0][0]))
                except:
                    synon = wn.synsets(w_to_replace[0][0])
                #print(synon) # all meanings
            # collect all synonyms from all meaning with the needed POS-Tag (as by word_to_translate) in the right order
                for el in synon:
                    a = el.lemma_names()
                    #print("a: ",a) # set of synonyms with one meaning
                    for el in a:
                        el = nltk.word_tokenize(el)
                        x = nltk.pos_tag(el)
                        if w_to_replace[0][1][0:2] == x[0][1][0:2]:
                            try:
                                if lancaster_stemmer.stem(w_to_replace[0][0].lower())!=lancaster_stemmer.stem(x[0][0].lower()):
                                    if x not in new_a:
                                        new_a.append(x)
                            except:
                                if w_to_replace[0][0].lower()!=x[0][0].lower():  
                                    if x not in new_a:
                                        new_a.append(x)
                                #print("DAA: ", w_to_replace[0][1][0:2],x[0][1][0:2])
                            #print("DAA2: ",lancaster_stemmer.stem(w_to_replace[0][0].lower()),lancaster_stemmer.stem(x[0][0].lower()))
                                if x not in new_a:
                                    new_a.append(x)
                    #print("new_a",new_a)   # all collected synonyms          
                if len(new_a)> 0:
                    #print("111")
                    number_of_syn = geom_distribution(len(new_a)) #what synonym to chose
                    alle.append(new_a[number_of_syn-1])
                else: # if we don't find good synonyms:
                    #print("222")
                    if count <len(new_clean_input): # try the next word in input
                        #print("223")                        
                        num +=1
                        count+=1
                        #print(num,count)
                    else: # if there are no more good synonyms to try for the current word:
                        #print("233")
                        new_a.append(w_to_replace) #use the same word (without replace)
                        alle.append(new_a[number_of_syn-1])
                        #pass

            else:
                num-=1
                count-=1
                #print("333")
                new_a.append(w_to_replace)
                alle.append(new_a[0])
    #print(len(alle)) # always = 1           
        if len(alle) > 0:
            #print("\nWord to repace: ",w_to_replace[0][0], "\nnew word: ", alle[0][0][0],"\n") 
            a = alle[0][0][0]
            if a.split("_"):
                x = ""
                a = a.split("_")
                for el in a:
                    x+=el
                    x+=" "
                x.strip()
                a = x
            #print("\n\nVOOORT ", new_clean_input,num)    
            s = new_clean_input[num][1]            
            if wo_to_replace==0:
                tra = ""
                our_input = our_input
            else:
                our_input = tra
                tra = ""
 
            for el in range(len(our_input.split(" "))):
                if el != s:
                    tra+=our_input.split(" ")[el]
                    tra+=" "
                else:
                    tra+=a
        else:
            tra=our_input
            print("No synsets for this sentence")
    
        num+=1
        count+=1
    print("- Input data:\n", our_input)
    print("\n- With Thesaurus:\n", tra)
    return tra
if __name__ == "__main__":
    thesaurus_right(our_input)



0.07098638248997406 0.5000019073559088
Number of words to replace:  1
0.5639006898771398 0.7741935483870968
- Input data:
 I have seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated.

- With Thesaurus:
 I let seen quite a few data augmentation techniques for image data. However, there's not been much work found online on data augmentation techniques for text data. Any suggestions in this regard will be appreciated. 


# Test - NB Classifier example

Load and unzip the first folder "Enron1" from the Enron Email Dataset (http://www2.aueb.gr/users/ion/data/enron-spam/ ) and specify the direction of the unzopped folder enron1 as DATA_DIR in the code below.

This folder (enron1) contains 3672 non-spam and 1500 spam emails. 

We use them for the binary classification.


In [221]:
import os
import re
import string
import math
 
#DATA_DIR = 'enron'
DATA_DIR = r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/enron"
target_names = ['ham', 'spam']
 
def get_data_enron(DATA_DIR):
#	subfolders = ['enron%d' % i for i in range(1,7)]
	subfolders = ['enron%d' % i for i in range(1,2)]
	data = []
	target = []
	for subfolder in subfolders:
		# spam
		spam_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'spam'))
		for spam_file in spam_files:
			with open(os.path.join(DATA_DIR, subfolder, 'spam', spam_file), encoding="latin-1") as f:
				data.append(f.read())
				target.append(1)
 
		# ham
		ham_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'ham'))
		for ham_file in ham_files:
			with open(os.path.join(DATA_DIR, subfolder, 'ham', ham_file), encoding="latin-1") as f:
				data.append(f.read())
				target.append(0)
 
	return data, target



In [219]:
class SpamDetector(object):
    """Implementation of Naive Bayes for binary classification"""
    def clean(self, s):
        translator = str.maketrans("", "", string.punctuation)
        return s.translate(translator)
 
    def tokenize(self, text):
        text = self.clean(text).lower()
        return re.split("\W+", text)
 
    def get_word_counts(self, words):
        word_counts = {}
        for word in words:
            word_counts[word] = word_counts.get(word, 0.0) + 1.0
        return word_counts
    
    def fit(self, X, Y):
        self.log_class_priors = {}
        self.word_counts = {}
        self.vocab = set()
 
        n = len(X)
        self.log_class_priors['spam'] = math.log(sum(1 for label in Y if label == 1) / n)
        self.log_class_priors['ham'] = math.log(sum(1 for label in Y if label == 0) / n)
        self.word_counts['spam'] = {}
        self.word_counts['ham'] = {}
 
        for x, y in zip(X, Y):
            c = 'spam' if y == 1 else 'ham'
            counts = self.get_word_counts(self.tokenize(x))
            for word, count in counts.items():
                if word not in self.vocab:
                    self.vocab.add(word)
                if word not in self.word_counts[c]:
                    self.word_counts[c][word] = 0.0
 
                self.word_counts[c][word] += count
    def predict(self, X):
        result = []
        for x in X:
            counts = self.get_word_counts(self.tokenize(x))
            spam_score = 0
            ham_score = 0
            for word, _ in counts.items():
                if word not in self.vocab: continue
            
                # add Laplace smoothing
                log_w_given_spam = math.log( (self.word_counts['spam'].get(word, 0.0) + 1) / (sum(self.word_counts['spam'].values()) + len(self.vocab)) )
                log_w_given_ham = math.log( (self.word_counts['ham'].get(word, 0.0) + 1) / (sum(self.word_counts['ham'].values()) + len(self.vocab)) )
 
                spam_score += log_w_given_spam
                ham_score += log_w_given_ham
 
            spam_score += self.log_class_priors['spam']
            ham_score += self.log_class_priors['ham']
 
            if spam_score > ham_score:
                result.append(1)
            else:
                result.append(0)
        return result

Prediction on the whole enron dataset:

In [222]:
if __name__ == '__main__':
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[100:], y[100:])
 
    pred = MNB.predict(X[:100])
    true = y[:100]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

KeyboardInterrupt: 

The prediction score accuracy on this large dataset is 0.95.

Let's do the same with our own small dataset.
We keep 63 first non-spam and first 54 spam emails from enron1.

In [223]:
DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own"

In [176]:
if __name__ == '__main__':
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[20:], y[20:])
 
    pred = MNB.predict(X[:20])
    true = y[:20]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

0.5500


It's clear that the accuracy on this small dataset is much lower = 0.55.

### Let's augment our spam and non-spam data with back-translation.

At first let's put the same small enron1 data set with just 63 first non-spam and first 54 spam emails in a new directory and specify it:

In [169]:
DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own_augmented_translation"

Create a back-translation function:

In [161]:
from mtranslate import translate
import os

target_names = ['ham', 'spam']

def back_translation(DATA_DIR, language):
#    subfolders = ['enron%d' % i for i in range(1,7)]
    subfolders = ['enron%d' % i for i in range(1,2)]
    data = []
    #target = []
    for subfolder in subfolders:
        # spam
        spam_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'spam'))
        for spam_file in spam_files:
            w = open(os.path.join(DATA_DIR, subfolder, 'spam', "new_"+spam_file), "a", encoding="utf-8")            
            with open(os.path.join(DATA_DIR, subfolder, 'spam', spam_file), encoding="utf-8") as f:
                data = f.readlines()
                for line in data:
                    try:
                    print("- Original english: \n", line)
                    german_translation = translate(line, language)
                    print("\n- German: \n", german_translation)
                    en_translation = translate(german_translation)
                    print("\n- English (new data): \n", en_translation)
                    print(en_translation,file=w)
            w.close()

 
        # ham
        ham_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'ham'))
        
        for ham_file in ham_files:
            w = open(os.path.join(DATA_DIR, subfolder, 'ham', "new_"+ham_file), "a", encoding="utf-8")
            with open(os.path.join(DATA_DIR, subfolder, 'ham', ham_file), encoding="utf-8") as f:
                data = f.readlines()
                #target = 0
                for line in data:
                    print("- Original english: \n", line)
                    german_translation = translate(line, language)
                    print("\n- German: \n", german_translation)
                    en_translation = translate(german_translation)
                    print("\n- English (new data): \n", en_translation)
                    print(en_translation,file=w)
            w.close()



if __name__ == '__main__':
    back_translation(DATA_DIR,"de")
 


- Original english: 
 Subject: christmas tree farm pictures


- German: 
 Betreff: Weihnachtsbaum Farm Bilder 


KeyboardInterrupt: 

Now our augmented dataset has 126 non-spam and 108 spam emails (and 1/2 of them are augmented).

Let's use Naive Base classifier on this augmented dataset:

In [ ]:
if __name__ == '__main__':
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[20:], y[20:])
 
    pred = MNB.predict(X[:20])
    true = y[:20]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

The accuracy is = 0.8500. It's higher that earlier.

Now let's compare it with the same amount of original spam emails from the enron1 dataset (126 non-spam, 108 spam).

In [149]:
DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/enron_original_small"

In [ ]:
if __name__ == '__main__':
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[20:], y[20:])
 
    pred = MNB.predict(X[:20])
    true = y[:20]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

The accuracy on the original sataset of the same size is = 0.90. That means that data augmentation with back translation works a bit worse than original data of the same size, but still better that the same classifier on the smaller amount of data.

### Let's augment our spam and non-spam data with thesarius.

At first let's put the same small enron1 data set with just 63 first non-spam and first 54 spam emails in a new directory and specify it:


In [224]:
import nltk
from nltk.corpus import wordnet as wn

DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own_augmented_thesarius"

And then run the code

In [225]:
import os

target_names = ['ham', 'spam']

def back_thesarius_enron(DATA_DIR):
#    subfolders = ['enron%d' % i for i in range(1,7)]
    subfolders = ['enron%d' % i for i in range(1,2)]
    data = []
    #target = []
    print(subfolders)
    for subfolder in subfolders:
        # spam
        spam_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'spam'))
        for spam_file in spam_files:
            w = open(os.path.join(DATA_DIR, subfolder, 'spam', "new_"+spam_file), "a", encoding="utf-8")            
            with open(os.path.join(DATA_DIR, subfolder, 'spam', spam_file), encoding="utf-8") as f:
                data = f.readlines()
                for line in data:
                    print("- Original english: \n", line)
                    translation = thesarius(line)
                    print("\n- German: \n", translation)
                    if translation != None:
                        print(translation,file=w)
            w.close()

 
        # ham
        ham_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'ham'))
        
        for ham_file in ham_files:
            w = open(os.path.join(DATA_DIR, subfolder, 'ham', "new_"+ham_file), "a", encoding="utf-8")
            with open(os.path.join(DATA_DIR, subfolder, 'ham', ham_file), encoding="utf-8") as f:
                data = f.readlines()
                #target = 0
                for line in data:
                    print("- Original english: \n", line)
                    translation = thesarius(line)
                    print("\n- German: \n", translation)
                    if translation != None:
                        print(translation,file=w)
            w.close()



if __name__ == '__main__':
    back_thesarius_enron(DATA_DIR)

['enron1']
- Original english: 
 Subject: dobmeos with hgh my energy level has gone up ! stukm



NameError: name 'thesarius' is not defined

Naive Bayes:

In [ ]:
if __name__ == '__main__':
    DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own_augmented_thesarius"
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[20:], y[20:])
 
    pred = MNB.predict(X[:20])
    true = y[:20]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

The accuracy is 0.9000. The results are similar to the results on the original dataset of the same size.
Thesarius works in this case a bit better (and more quickly) than back translation, but can sometimes cause overfitting (because not all the words are replaced with their synonims). Back translation can augment more data, when we use several target languages for the back-translation.

And with new Version of Thesaurus with geometrical distribution: (thesaurus_right)

In [226]:
import nltk
from nltk.corpus import wordnet as wn

DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own_augmented_thesaurus2"
print("d")

d


In [214]:
import os

target_names = ['ham', 'spam']

def back_thesaurus_enron2(DATA_DIR):
#    subfolders = ['enron%d' % i for i in range(1,7)]
    subfolders = ['enron%d' % i for i in range(1,2)]
    data = []
    #target = []
    for subfolder in subfolders:
        print("\n sub: ",subfolder)
        # spam
        spam_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'spam'))
        for spam_file in spam_files:
            print(spam_file)
            w = open(os.path.join(DATA_DIR, subfolder, 'spam', "new_"+spam_file), "a", encoding="utf-8") 
            #print(w)
            with open(os.path.join(DATA_DIR, subfolder, 'spam', spam_file), encoding="utf-8") as f:
                data = f.readlines()
                for line in data:
                    print("- Original english: \n", line)
                    translation = thesaurus_right(line)
                    print("\n- Thesaurus2: \n", translation)
                    if translation != None:
                        print(translation,file=w)
            w.close()

 
        # ham
        #print("here")
        ham_files = os.listdir(os.path.join(DATA_DIR, subfolder, 'ham'))
        
        for ham_file in ham_files:
            print(ham_file)
            w = open(os.path.join(DATA_DIR, subfolder, 'ham', "new_"+ham_file), "a", encoding="utf-8")
            with open(os.path.join(DATA_DIR, subfolder, 'ham', ham_file), encoding="utf-8") as f:
                data = f.readlines()
                #target = 0
                for line in data:
                    print("- Original english: \n", line)
                    translation = thesaurus_right(line)
                    print("\n- Thesaurus: \n", translation)
                    if translation != None:
                        print(translation,file=w)
            w.close()



if __name__ == '__main__':
    back_thesaurus_enron2(DATA_DIR)
    print("DONE")


 sub:  enron1
0006.2003-12-18.GP.spam.txt
- Original english: 
 Subject: dobmeos with hgh my energy level has gone up ! stukm

0.2762681094304525 0.5079365079365079
Number of words to replace:  1
- Input data:
 Subject: dobmeos with hgh my energy level has gone up ! stukm


- With Thesaurus:
 open dobmeos with hgh my energy level has gone up ! stukm
 

- Thesaurus2: 
 open dobmeos with hgh my energy level has gone up ! stukm
 
- Original english: 
 introducing

Number of words to replace:  1
- Input data:
 introducing


- With Thesaurus:
 enclose 

- Thesaurus2: 
 enclose 
- Original english: 
 doctor - formulated

0.02759004165422606 0.6666666666666666
Number of words to replace:  1
0.5420382620780992 0.750022888882107
- Input data:
 doctor - formulated


- With Thesaurus:
 physician - formulated
 

- Thesaurus2: 
 physician - formulated
 
- Original english: 
 hgh


- Thesaurus2: 
 hgh

- Original english: 
 human growth hormone - also called hgh

0.13333053487167187 0.5161290322580

- Input data:
 - controlled mood swings


- With Thesaurus:
 - ensure mood swings
 

- Thesaurus2: 
 - ensure mood swings
 
- Original english: 
 - new hair growth and color restore

0.5589059153823698 0.7741935483870968
Number of words to replace:  2
0.23969737551960343 0.5039370078740157
- Input data:
 - young hair growth and color restore
 

- With Thesaurus:
 - young hair's-breadth growth and color restore
  

- Thesaurus2: 
 - young hair's-breadth growth and color restore
  
- Original english: 
 read

Number of words to replace:  1
0.45248537431502467 0.5019607843137255
- Input data:
 read


- With Thesaurus:
 learn 

- Thesaurus2: 
 learn 
- Original english: 
 more at this website

Number of words to replace:  2
0.6313175131351174 0.8571428571428571
- Input data:
 more at this internet site 

- With Thesaurus:
 more at this website site  

- Thesaurus2: 
 more at this website site  
- Original english: 
 unsubscribe


- Thesaurus2: 
 unsubscribe

0008.2003-12-18.GP.spam.txt
- O

0.35660137884293147 0.5
Number of words to replace:  1
0.5476023889563424 0.7529411764705882
- Input data:
 at the moment , we will be requiring your assistance in a matter that involves investment of monies , which we intend to transfer to your account , upon clarification and a workable agreement reached in consummating the project with you . based on a recommendation from an associate concerning your integrity , loyalty and understanding , we deemed it necessary to contact you accordingly . all arrangements in relation to this investment initiative , as well as the initial capital for its take off has been tactically set aside to commence whatever business you deemed fit , that will turn around profit favourably . we request you immediately contact us if you will be favorably disposed to act as a partner in this venture , and possibly will afford us the opportunity to discuss whatever proposal you may come up with . also


- With Thesaurus:
 at the instant , we will be requiring you

0.834937770967559 0.8750000000000002
Number of words to replace:  3
0.244629556902035 0.5039370078740157
0.22108693624441553 0.6666666666666666
- Input data:
 such Brobdingnagian sum of funds , without arousing suspicion from any quarter as a drug or terrorist related funds ; and this will assist us in the long run to forestall any form of investigations . remember that , on no account must we be seen or perceived to be directly connected with the transfer of funds . you will be the one to be doing all these , and in the course of transfer , if for any reason whatsoever , you incurred some bills , we shall adequately retire same , upon the successful confirmation of the funds in your account . the commencement of this project is based on your ability to convince us of the need to invest in whatever business you have chosen , and to trust your personality and status , especially as it concerns the security of the
  

- With Thesaurus:
 such Brobdingnagian sum of funds , without kindle s

0.5208883657547317 0.750733137829912
Number of words to replace:  2
0.3565157268102588 0.5000038147263697
- Input data:
 capital of Indiana , in - race car simulators ? and baldacci sign agreement to develop international markets for the new generation race simulutors
 

- With Thesaurus:
 capital of Indiana , subspecies - race car simulators ? and baldacci sign agreement to develop international markets for the new generation race simulutors
  

- Thesaurus2: 
 capital of Indiana , subspecies - race car simulators ? and baldacci sign agreement to develop international markets for the new generation race simulutors
  
- Original english: 
 08 / 12 / 2003


- Thesaurus2: 
 08 / 12 / 2003

- Original english: 
 indianapolis , in - imts forms new subsidiary for manufacturing and sales of race car simulators

0.32564892092467973 0.5079365079365079
Number of words to replace:  1
- Input data:
 indianapolis , in - imts forms new subsidiary for manufacturing and sales of race car simulators



...

Number of words to replace:  2
0.8347033329161182 0.9032258064516129
- Input data:
 no former transactions at this meter since 1 / 98 .
 

- With Thesaurus:
 no former transactions at this beat since 1 / 98 .
  

- Thesaurus: 
 no former transactions at this beat since 1 / 98 .
  
- Original english: 
 some questions i need answered are - why was volume allocated to transport

0.4772450032956165 0.5019607843137255
Number of words to replace:  1
0.3148458692262305 0.5079365079365079
- Input data:
 some questions i need answered are - why was volume allocated to transport


- With Thesaurus:
 some questions iodine need answered are - why was volume allocated to transport
 

- Thesaurus: 
 some questions iodine need answered are - why was volume allocated to transport
 
- Original english: 
 contracts through 10 / 31 / 97 and then started to be allocated to the 089

0.297346773110884 0.5333333333333333
Number of words to replace:  1
- Input data:
 contracts through 10 / 31 / 97 and then s

Number of words to replace:  4
0.30993169502819723 0.6666666666666666
0.20119838133047172 0.5079365079365079
0.6516417784148228 0.7741935483870968
0.4602149743023098 0.5002442598925256
- Input data:
 from : Frank liter Esther Hobart McQuigg Slack Morris morris 12 / 16 / 99 06 : 04 pm
   

- With Thesaurus:
 from : Frank liter Esther Hobart McQuigg Slack Morris morris 12 / 16 autopsy 99 06 : 04 pm
    

- Thesaurus: 
 from : Frank liter Esther Hobart McQuigg Slack Morris morris 12 / 16 autopsy 99 06 : 04 pm
    
- Original english: 
 to : daren j farmer / hou / ect @ ect

Number of words to replace:  4
0.45328438192056736 0.5079365079365079
0.4513138008908978 0.5714285714285714
0.189131767822273 0.5714285714285714
- Input data:
 to : daren watt husbandman farmer / hou electroconvulsive therapy ect @ ect
   

- With Thesaurus:
 to : daren watt husbandman farmer / hou electroconvulsive therapy electroconvulsive therapy @ ect
    

- Thesaurus: 
 to : daren watt husbandman farmer / hou ele

0.4323556082252628 0.6666666666666666
Number of words to replace:  1
0.5036314461583429 0.7500028610338632
- Input data:
 subject : jan noms


- With Thesaurus:
 theme : jan noms
 

- Thesaurus: 
 theme : jan noms
 
- Original english: 
 ( see attached file : egmnom - jan . xls )

0.44629349781085637 0.5161290322580645
Number of words to replace:  1
0.4377925193188446 0.5333333333333333
- Input data:
 ( see attached file : egmnom - jan . xls )


- With Thesaurus:
 ( realize attached file : egmnom - jan . xls )
 

- Thesaurus: 
 ( realize attached file : egmnom - jan . xls )
 
- Original english: 
 - egmnom - jan . xls
Number of words to replace:  2
- Input data:
 - egmnom - January . xls 

- With Thesaurus:
 - egmnom - January . twoscore  

- Thesaurus: 
 - egmnom - January . twoscore  
0077.1999-12-28.farmer.ham.txt
- Original english: 
 Subject: black marlin - meter 986782 for 8 / 98 - ua 4

0.5074866687083001 0.5333333333333333
Number of words to replace:  1
0.4941251542267705 0.571

0.06710839464989697 0.5714285714285714
- Input data:
 buy / sell : buy


- With Thesaurus:
 buy / deal : buy
 

- Thesaurus: 
 buy / deal : buy
 
- Original english: 
 ctpty : aquila energy marketing corporation

0.848825009871369 0.9333333333333333
Number of words to replace:  3
0.33852380201593935 0.5714285714285714
0.7399195371264486 0.7501831501831502
0.6285192172628961 0.8571428571428571
- Input data:
 ctpty : L'Aquila vigor marketing corporation
  

- With Thesaurus:
 ctpty : L'Aquila vigor commercialize corporation
   

- Thesaurus: 
 ctpty : L'Aquila vigor commercialize corporation
   
- Original english: 
 zone : agua dulce @ 0584

0.5543763273853545 0.6666666666666666
Number of words to replace:  1
0.26873675536401476 0.5714285714285714
- Input data:
 zone : agua dulce @ 0584


- With Thesaurus:
 geographical zone : agua dulce @ 0584
 

- Thesaurus: 
 geographical zone : agua dulce @ 0584
 
- Original english: 
 volume : 5 , 000 / d

0.08865614461710887 0.6666666666666666
Num

0.07680341265396047 0.5161290322580645
0.15428423105191147 0.5039370078740157
0.31530007257741577 0.5161290322580645
0.6969818893698619 0.7559055118110236
0.19044514031790682 0.5161290322580645
0.24663925672583 0.5001221001221001
- Input data:
 we get kettle of fish the dissemble paths get rectify have encipher thus code so this won ' t
       

- With Thesaurus:
 we get kettle of fish the dissemble paths get rectify have encipher thus code South Korean won this won ' t
        

- Thesaurus: 
 we get kettle of fish the dissemble paths get rectify have encipher thus code South Korean won this won ' t
        
- Original english: 
 happen any more . below is a screen print of the nov 22 problem that is now

0.8823226581658737 0.9393346379647749
Number of words to replace:  4
0.6671288430842311 0.8571428571428571
0.21631796780083054 0.5000038147263697
0.036960717098876716 0.5333333333333333
- Input data:
 find any more . below be a silver screen print of the nov 22 problem that is now
  

In [215]:
if __name__ == '__main__':
    DATA_DIR =r"C:/Users/cher061/My_Job/Projects/Data_Augmentation/own_augmented_thesaurus2"
    X, y = get_data_enron(DATA_DIR)
    MNB = SpamDetector()
    MNB.fit(X[20:], y[20:])
 
    pred = MNB.predict(X[:20])
    true = y[:20]
 
    accuracy = sum(1 for i in range(len(pred)) if pred[i] == true[i]) / float(len(pred))
    print("{0:.4f}".format(accuracy))

1.0000


Accuracy = 100% (overfitting)

## Let's experiment with other Datasets:

- 20 Newsgoups

Statistics: 11293 train docs, 7528 test docs, total 18821 docs.

Extract data and targets from the dataset:

In [227]:
#categories = ['alt.atheism', 'comp.graphics', 'comp.os.ms-windows.misc','comp.sys.ibm.pc.hardware','comp.sys.mac.hardware',
#                'comp.windows.x','misc.forsale','rec.autos','rec.motorcycles','rec.sport.baseball','rec.sport.hockey',
#                'sci.crypt','sci.electronics','sci.med','sci.space','soc.religion.christian','talk.politics.guns',
#                'talk.politics.mideast','talk.politics.misc','talk.religion.misc']
categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']
from sklearn.datasets import fetch_20newsgroups
twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
print(twenty_train.target_names)
len(twenty_train.data)
len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])


['alt.atheism', 'comp.graphics', 'sci.med', 'talk.religion.misc']


2035

Multiclass Naive Bayes:

In [230]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from sklearn.naive_bayes import MultinomialNB
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

Pipeline(memory=None,
     steps=[('vect', CountVectorizer(analyzer='word', binary=False, decode_error='strict',
        dtype=<class 'numpy.int64'>, encoding='utf-8', input='content',
        lowercase=True, max_df=1.0, max_features=None, min_df=1,
        ngram_range=(1, 1), preprocessor=None, stop_words=None,
        strip...inear_tf=False, use_idf=True)), ('clf', MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True))])

In [231]:
import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)    

0.829520295202952

SVM

In [232]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)   

0.8656826568265683

In [233]:
from sklearn import metrics
print(metrics.classification_report(twenty_test.target, predicted,
target_names=twenty_test.target_names))

                    precision    recall  f1-score   support

       alt.atheism       0.80      0.87      0.83       319
     comp.graphics       0.86      0.97      0.91       389
           sci.med       0.94      0.87      0.90       396
talk.religion.misc       0.86      0.70      0.77       251

       avg / total       0.87      0.87      0.86      1355



In [234]:
metrics.confusion_matrix(twenty_test.target, predicted)

array([[276,  12,   9,  22],
       [  3, 378,   4,   4],
       [  9,  41, 343,   3],
       [ 56,  11,   8, 176]], dtype=int64)

Let's do the same on the small amount of data (100 train docs):

In [235]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)


text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data[:100], twenty_train.target[:100])

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.4317343173431734

Result is 0.4317343173431734

... on 200 train docs:

In [66]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data[:200], twenty_train.target[:200])

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5771217712177121

Result is 0.5771217712177121


... on 300 train docs:

In [65]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data[:300], twenty_train.target[:300])

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.7298892988929889

Result is 0.7298892988929889


And the same for SVM with

...100 train docs:

In [80]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)


from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data[:100], twenty_train.target[:100])  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.6701107011070111

Performance is 0.6701107011070111

...200 train docs:

In [81]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data[:200], twenty_train.target[:200])  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.7247232472324723

Performance is 0.7247232472324723

...300 docs:

In [82]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data[:300], twenty_train.target[:300])  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.7955719557195572

Performance is 0.7955719557195572

Not let's start augmenting the data

...with back-translation:

We'll take the 100 train examples and for each of these examples we'll create a similar text fragment with back translation:

In [83]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    #new_data_back_transl.append(new)
    #new_targets.append(twenty_train.target[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)




0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
200
200


Now we have 200 train examples. Let's try NB on them:

In [84]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5136531365313654

Performance is 0.5136531365313654. It's comparable with the performance of 200 train examples of the original dataset (0.5771217712177121)

And now the same for SVM:

In [85]:
#print(len(twenty_train.data))
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

200


0.6856088560885609

Performance is 0.6856088560885609. 

It's comparable with the performance of SVM of 200 train examples of the original dataset (0.7247232472324723)

Let's use one more target language ('fr') and together with "en" create 300 train documents from 100:

In [86]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    fr_transl = translate(twenty_train.data[i], "fr")
    new1 = translate(fr_transl, "en")
    (twenty_train.data).append(new1)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
300
300


Now we have 300 train examples. Let's try NB on them:

In [87]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5616236162361624

Performance is 0.5616236162361624. 
It's smaller than the performance of 300 train examples of the original dataset (0.7298892988929889).
Using french as a target language together with english doesn't give good results.

And now the same for SVM:

In [88]:
#print(len(twenty_train.data))
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.6952029520295203

Performance is 0.6952029520295203

It's also smaller than the performance of SVM of 300 train examples of the original dataset (0.7955719557195572)


Now let's do the same using Thesarius Data Augmentation:

In [91]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    new = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
200
200


Now we have 200 train examples.
Let's try NB on them:

In [92]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5321033210332103

Performance is 0.5321033210332103. It's comparable with the performance of 200 train examples of the original dataset (0.5771217712177121)

In [ ]:
And SVM:

In [93]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.7077490774907749

Performance is 0.7077490774907749

It's comparable with the performance of SVM of 200 train examples of the original dataset (0.7247232472324723)


...Let's du the same with Thesaurus with geometrical distribution:

In [236]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    new = thesaurus_right(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
Number of words to replace:  2
- Input data:
 From: vdp@mayo.edu (Vinayak Dutt)
Subject: rhenium Islamic Banks (was Re: Slavery
Reply-To: vdp@mayo.edu
Organization: Mayo Foundation/Mayo Graduate School :Rochester, MN
Lines: 39

In article 28833@monu6.cc.monash.edu.au,  darice@yoyo.cc.monash.edu.au (Fred Rice) writes:
#In <1993Apr14.143121.26376@bmw.mayo.edu> vdp@mayo.edu (Vinayak Dutt) writes:
#>So instead of calling it interest on deposits, you call it *returns on investements*
#>and instead of calling loans you call it *investing in business* (that is in other words
#>floating stocks in your company). 
#
#No, interest is different from a return on an investment.  For one
#thing, a return on an investment has greater risk, and not a set return
#(i.e. the amount of money you make can go up or down, or you might even
#lose money).  The difference is, the risk of loss is shared by the
#investor, rather than practically all the risk being taken by the
#borrower when the borrower borrows

Number of words to replace:  1
- Input data:
 From: med50003@nusunix1.nus.sg (WANSAICHEONG KHIN-LIN)
Subject: Re: MORBUS MENIERE - is there a real remedy?
Organization: National University of Singapore
X-Newsreader: TIN [version 1.1 PL6]
Lines: 21

It would be nice to think that individuals can somehow 'beat the system'
and like a space explorer, boldly go where no man has gone before and
return with a prize cure. Unfortunately, too often the prize is limited
and the efficacy of the 'cure' questionable when applied to all
sufferers.

This applies to both medical researchers and non-medical individuals.
Just because it appears in an obscure journal and may be of some use
does not make the next cure-all. What about the dozens of individuals
who have courageously participated in clinical trials? Did they have any
guarentee of cures? Are they any less because they didn't trumpet their
story all over the world?

As a parting note, wasn't there some studies done on Gingko seeds for
Meniere's

Number of words to replace:  1
- Input data:
 From: halat@pooh.bears (Jim Halat)
Subject: Re: After 2000 years, can we say that Christian Morality is
Reply-To: halat@pooh.bears (Jim Halat)
Lines: 45

In article <1r3qab$o1v@horus.ap.mchp.sni.de>, frank@D012S658.uucp (Frank O'Dwyer) writes:
>In article <930421.102525.9Y9.rusnews.w165w@mantis.co.uk> mathew <mathew@mantis.co.uk> writes:
>#frank@D012S658.uucp (Frank O'Dwyer) writes:
>#> In article <930420.100544.6n0.rusnews.w165w@mantis.co.uk> mathew
>#> <mathew@mantis.co.uk> writes:
>#> #This is complete nonsense.  Relativism means saying that there is no absolut
>#> #standard of morality; it does NOT mean saying that all standards of morality
>#> #are equally good.
>#> 
>#> Presumably this means that some moral systems are better than others?
>#> How so?  How do you manage this without an objective frame of reference?
>#

Either Frank O'Dwyer or mathew said:

[...stiff deleted...]

>#Which goes faster, a bullet or a snail?  How come you c

Number of words to replace:  2
- Input data:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: atomic number 75 Yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg
 

- With Thesaurus:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: atomic as yet 75 Yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg
  
10
Number of word

Number of words to replace:  2
- Input data:
 From: ds0007@medtronic.COM (Dale metre Skiba)
Subject: Re: JUDAS, CRUCIFIXION, TYRE, Etc...
Nntp-Posting-Host: bass.pace.medtronic.com
Organization: Medtronic, Inc.
X-Newsreader: TIN [version 1.1 PL8]
Lines: 43

David Joslin (joslin@pogo.isp.pitt.edu) wrote:
: af664@yfn.ysu.edu (Frank DeCenso, Jr.) writes:
: >Based on the amount of E-Mail from fellow Christians who have read the
: >posts and told me I was wasting my time with Butler and Joslin, I told
: >them I wasn't doing it for DB or  DJ but for other Christians.  They
: >have told me that DB's and DJ's arguments won't convince most Bible
: >studying Christians.  So I have reevaluated my purpose here and it's
: >also contributed to my decision.

: So most Bible-studying Christians won't be convinced by my arguments? 
: And this is supposed to be a Good Thing, I presume?

Where does this "Most Bible studying Christians think as Frank
does" come from.  And what implied "good" are you doing

...

Number of words to replace:  1
- Input data:
 From: rind@enterprise.bih.harvard.edu (David Rind)
Subject: Re: Arrhythmia
Organization: Beth Israel Hospital, Harvard Medical School, Boston Mass., USA
Lines: 26
NNTP-Posting-Host: enterprise.bih.harvard.edu

In article <1993Apr22.205509.23198@husc3.harvard.edu>
 perry1@husc10.harvard.edu (Alexis Perry) writes:
>In article <1993Apr22.031423.1@vaxc.stevens-tech.edu>
 u96_averba@vaxc.stevens-tech.edu writes:

>>doctors said that he could die from it, and the medication caused

>	Is it that serious?  My EKG often comes back with a few irregular
>beats.  Another question:  Is a low blood potassium level very bad?  My
>doctor seems concerned, but she tends to worry too much in general.

The term arrhythmia is usually used to encompass a wide range of abnormal
heart rhythms (cardiac dysrhythmias).  Some of them are very serious
while others are completely benign.  Having "a few irregular beats"
on an EKG could be serious depending on what those 

Number of words to replace:  2
- Input data:
 From: irfan@davinci.ece.wisc.edu (Irfan Alan)
Subject: A TREATISE ON THE MIRACLES OF Elijah Muhammad SAW, PART-1
Organization: Univ. of Wisconsin-Madison; Electrical & Computer Engineering
Distribution: usa
Lines: 81

DROPLET VOL 1, No 11, Part 1

A  D R O P L E T
From The Vast Ocean Of The Miraculous Qur'an

Translations from the Arabic and Turkish Writings of 
Bediuzzaman Said Nursi, The Risale-i Noor

VOL 1, No 11, Part 1
------------------------------------------------------------------


   		 NINETEENTH LETTER  

		 MU'JIZAT-I AHMEDIYE RISALESI 
(A TREATISE ON THE MIRACLES OF MUHAMMAD SAW)       
(SAW: PEACE AND BLESSINGS BE UPON HIM)

In His Name (ALLAH) , Be He (ALLAH) Glorified!
There is Nothing But Glorifies His (ALLAH's) Praise.

In The Name Of  Allah, The Compassionate, The Merciful

   "He is who has sent His Messenger with
guidance and the religion of truth  to make it
supreme over all religion:  and sufficient is Allah
as a W

Number of words to replace:  1
- Input data:
 From: kjiv@lrc.edu
Subject: Hismanal, et. al.--side effects
Organization: Lenoir-Rhyne College, Hickory, NC
Lines: 22

Can someone tell me whether or not any of the following medications 
has been linked to rapid/excessive weight gain and/or a distorted 
sense of taste or smell:  Hismanal; Azmacort (a topical steroid to 
prevent asthma); Vancenase.

Also:
You may have guessed, I'm an allergy sufferer--but I'm beginning to 
suspect I'm also the victim of a Dr. toliberal with the prescription 
p. The allergist I went to last Oct. simply inquired about my symptons 
( I was suffering chronic asthma attacks), gave me a battery of 
allergy tests, and went down a checklist of drugs (a photocopied 
sheet).  I've gained out 30 lbs. since then though I haven't eaten 
more or much differently than before; I'vsuffered depression; , 
fatigue; and I've experienced a foul smell and sense of taste for 
about the last two months.  I mentioned the lack of sm

Number of words to replace:  2
- Input data:
 From: Mark-Tarbell@suite.com
Subject: amnio et. al.
Organization: Suite Software
Lines: 7
Reply-To: suite!tarbell@uunet.uu.net
NNTP-Posting-Host: gilgamesh.suite.com

Is there some difference between the purposes behind
amniocentesis and chorionic villi sampling? They sound
similar to me, but are intended to detect different
things?

Thanks.

 

- With Thesaurus:
 From: Mark-Tarbell@suite.com
Subject: amnio et. aluminium Suite Software
Lines: 7
Reply-To: suite!tarbell@uunet.uu.net
NNTP-Posting-Host: gilgamesh.suite.com

Is there some difference between the purposes behind
amniocentesis and chorionic villi sampling? They sound
similar to me, but are intended to detect different
things?

Thanks.

  
97
Number of words to replace:  1
- Input data:
 From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: [soc.motss, et al.] "Princeton axes matching funds for Boy Scouts"
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcforum Unix Users G

Number of words to replace:  1
- Input data:
 From: turner@reed.edu (Havok impersonated)
Subject: Re: Is MSG sensitivity superstition?
Article-I.D.: reed.1993Apr16.170752.6312
Organization: Reed College, Portland, OR
Lines: 35

In article <1qlgdrINN79b@gap.caltech.edu> carl@SOL1.GPS.CALTECH.EDU writes:
>In article <1993Apr15.173902.66278@cc.usu.edu>, slyx0@cc.usu.edu writes:
>=Surprise surprise, different people react differently to different things. One
>=slightly off the subject case in point. My brother got stung by a bee. I know
>=he is allergic to bee stings, but that his reaction is severe localized
>=swelling, not anaphylactic shock. I could not convince the doctors of that,
>=however, because that's not written in their little rule book.
>Of course, bee venom isn't a single chemical.  Could be your brother is
>reacting to a different component than the one that causes anaphylactic shock
>in other people.

Hmmm.  The last time I got stung by a bee I experienced the same reaction

Now we have 200 train examples. Let's try NB on them:

In [237]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5527675276752767

Performance is  0.5527675276752767. With Thesaurus without geom.distribution it was 0.5321033210332103. We see 2% improvement. It's comparable with the performance of 200 train examples of the original dataset (0.5771217712177121)

And SVM:

In [238]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.7025830258302583

Performance is 0.7025830258302583. With Thesaurus without geometrical distribution it was 0.7077490774907749.
We see 0,5% decrease.

The performance of SVM of 200 train examples of the original dataset was 0.7247232472324723


Now let's have a look at the combination of Back-Translation with Thesarius:

In [94]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    new1 = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new1)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
300
300


Now we have 300 train examples. Let's try NB on them:

In [95]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.5579335793357934

Performance is 0.5579335793357934. 
It's smaller than the performance of 300 train examples of the original dataset (0.7298892988929889). 

And SVM:

In [97]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.6966789667896679

Performance is 0.6966789667896679

It's also smaller than the performance of SVM of 300 train examples of the original dataset (0.7955719557195572)


Let's try to use a larger amount of input original Data (2000 train documents) and try to compare the performance with 1000 original and 1000 augmented examples:

In [239]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:2000]
twenty_train.target = twenty_train.target[:2000]

#new_data_back_transl = []
#new_targets = []


print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

2000
2000


NB on 2000 original train data:

In [106]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.8287822878228782

Performance is 0.8287822878228782

and SVM on original train data:

In [107]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.8605166051660517

Performance is 0.8605166051660517

Augmenting with en Back-translation:

In [112]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])

#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131


HTTPError: HTTP Error 413: Request Entity Too Large

Augmenting with Thesarius

In [109]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    new = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])

#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

We have got 2000 train examples. NB:

In [110]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.8383763837638376

Performance is 0.8383763837638376. It's even a bit better than NB on original 2000 train docs (0.8287822878228782)

And now SVM:

In [111]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.844280442804428


Performance is 0.844280442804428. It's comparable to the performance of th original data (0.8605166051660517)

..And now Thesaurus with geometrical distribution:

In [240]:
from mtranslate import translate
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
#print(twenty_train.target_names)
#len(twenty_train.data)
#len(twenty_train.filenames)

#print(twenty_train.data[:1])
#print(twenty_train.target[:1])
twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

#new_data_back_transl = []
#new_targets = []

for i in range(len(twenty_train.data)):
    print(i)
    new = thesaurus_right(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])

#print(new_data_back_transl[:2])
#print(new_targets[:2])
print(len(twenty_train.data))
print(len(twenty_train.target))

# Example hoe to append data
#a = twenty_train.data[:2]
#b = twenty_train.target[:2]

#a.append("f")
#b = np.append(b,[0])

#print(a)
#print(b)

0
Number of words to replace:  1
- Input data:
 From: vdp@mayo.edu (Vinayak Dutt)
Subject: Re: Islamic Banks (was Re: Slavery
Reply-To: vdp@mayo.edu
Organization: Mayo Foundation/Mayo Graduate School :Rochester, MN
Lines: 39

In article 28833@monu6.cc.monash.edu.au,  darice@yoyo.cc.monash.edu.au (Fred Rice) writes:
#In <1993Apr14.143121.26376@bmw.mayo.edu> vdp@mayo.edu (Vinayak Dutt) writes:
#>So instead of calling it interest on deposits, you call it *returns on investements*
#>and instead of calling loans you call it *investing in business* (that is in other words
#>floating stocks in your company). 
#
#No, interest is different from a return on an investment.  For one
#thing, a return on an investment has greater risk, and not a set return
#(i.e. the amount of money you make can go up or down, or you might even
#lose money).  The difference is, the risk of loss is shared by the
#investor, rather than practically all the risk being taken by the
#borrower when the borrower borrows fro

Number of words to replace:  1
- Input data:
 From: med50003@nusunix1.nus.sg (WANSAICHEONG KHIN-LIN)
Subject: Re: MORBUS MENIERE - is there a real remedy?
Organization: National University of Singapore
X-Newsreader: TIN [version 1.1 PL6]
Lines: 21

It would be nice to think that individuals can somehow 'beat the system'
and like a space explorer, boldly go where no man has gone before and
return with a prize cure. Unfortunately, too often the prize is limited
and the efficacy of the 'cure' questionable when applied to all
sufferers.

This applies to both medical researchers and non-medical individuals.
Just because it appears in an obscure journal and may be of some use
does not make the next cure-all. What about the dozens of individuals
who have courageously participated in clinical trials? Did they have any
guarentee of cures? Are they any less because they didn't trumpet their
story all over the world?

As a parting note, wasn't there some studies done on Gingko seeds for
Meniere's

Number of words to replace:  3
- Input data:
 From: halat@pooh.bears (Jim Halat)
Subject: rhenium After 2000 years, can we say that Christian ethics is
Reply-To: halat@pooh.bears (Jim Halat)
Lines: 45

In article <1r3qab$o1v@horus.ap.mchp.sni.de>, frank@D012S658.uucp (Frank O'Dwyer) writes:
>In article <930421.102525.9Y9.rusnews.w165w@mantis.co.uk> mathew <mathew@mantis.co.uk> writes:
>#frank@D012S658.uucp (Frank O'Dwyer) writes:
>#> In article <930420.100544.6n0.rusnews.w165w@mantis.co.uk> mathew
>#> <mathew@mantis.co.uk> writes:
>#> #This is complete nonsense.  Relativism means saying that there is no absolut
>#> #standard of morality; it does NOT mean saying that all standards of morality
>#> #are equally good.
>#> 
>#> Presumably this means that some moral systems are better than others?
>#> How so?  How do you manage this without an objective frame of reference?
>#

Either Frank O'Dwyer or mathew said:

[...stiff deleted...]

>#Which goes faster, a bullet or a snail?  How come you

Number of words to replace:  2
- Input data:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: rhenium Yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg
 

- With Thesaurus:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: rhenium as yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg
  
10
Number of words to replace:  

Number of words to replace:  6
- Input data:
 From: ds0007@medtronic.COM (Dale one thousand atomic St. excruciation Sur Re: JUDAS, CRUCIFIXION, TYRE, Etc...
Nntp-Posting-Host: bass.pace.medtronic.com
Organization: Medtronic, Inc.
X-Newsreader: TIN [version 1.1 PL8]
Lines: 43

David Joslin (joslin@pogo.isp.pitt.edu) wrote:
: af664@yfn.ysu.edu (Frank DeCenso, Jr.) writes:
: >Based on the amount of E-Mail from fellow Christians who have read the
: >posts and told me I was wasting my time with Butler and Joslin, I told
: >them I wasn't doing it for DB or  DJ but for other Christians.  They
: >have told me that DB's and DJ's arguments won't convince most Bible
: >studying Christians.  So I have reevaluated my purpose here and it's
: >also contributed to my decision.

: So most Bible-studying Christians won't be convinced by my arguments? 
: And this is supposed to be a Good Thing, I presume?

Where does this "Most Bible studying Christians think as Frank
does" come from.  And what implied "

...

Number of words to replace:  2
- Input data:
 From: Keb (Gordon Banks)
Subject: Re: request for information on "essential tremor" and Indrol?
Reply-To: geb@cs.pitt.edu (Gordon Banks)
Organization: Univ. of Pittsburgh Computer Science
Lines: 12

In article <1q1tbnINNnfn@life.ai.mit.edu> sundar@ai.mit.edu writes:

Essential tremor is a progressive hereditary tremor that gets worse
when the patient tries to use the effected member.  All limbs, vocal
cords, and head can be involved.  Inderal is a beta-blocker and
is usually effective in diminishing the tremor.  Alcohol and mysoline
are also effective, but alcohol is too toxic to use as a treatment.
-- 
----------------------------------------------------------------------------
Gordon Banks  N3JXP      | "Skepticism is the chastity of the intellect, and
geb@cadre.dsl.pitt.edu   |  it is shameful to surrender it too soon." 
----------------------------------------------------------------------------
 

- With Thesaurus:
 From: Keb (Gordon B

Number of words to replace:  2
- Input data:
 From: teckjoo@iti.gov.sg (Chua Teck Joo)
Subject: Visuallib (3D graphics for Windows)
Organization: entropy Technology Institute, National Computer Board, Singapore.
Lines: 17


I am currently looking for a 3D graphics library that runs on MS
Windows 3.1.  Are there any such libraries out there other than
Visuallib?  (It must run on VGA and should not require any other
add-on graphics cards).

For Visuallib, will it run with Metaware High C compiler v3.0?  Any
email contact for the author of Visuallib?

Any help would be much appreciated.  Thanks.


-- 
* Chua, Teck Joo	    | Information Technology Institute *
* Email: teckjoo@iti.gov.sg | 71 Science Park Drive	       *
* Phone: (65) 772-0237 	    | Singapore (0511)		       *
* Fax:   (65) 779-1827      |			   	       *
 

- With Thesaurus:
 From: teckjoo@iti.gov.sg (Chua Teck Joo)
Subject: Visuallib (3D graphics for Windows)
Organization: entropy applied science Institute, National Compute

Number of words to replace:  3
- Input data:
  wupost!uunet!olivea!sgigate!sgi!fido!solntze.wpd.sgi.com!livesey
Subject: rhenium >>>>>>Pompous nates livesey@solntze.wpd.sgi.com (Jon Livesey)
 <93089.050046MVS104@psuvm.psu.edu> <1pa6ntINNs5d@gap.caltech.edu> 
 <1993Mar30.210423.1302@bmerh85.bnr.ca> <1pcnqjINNpon@gap.caltech.edu> <kmr4.1344.733611641@po.CWRU.edu> <1pi9btINNqa5@gap.calte
Organization: sgi
NNTP-Posting-Host: solntze.wpd.sgi.com
Lines: 20

In article <1pi9btINNqa5@gap.caltech.edu>, keith@cco.caltech.edu (Keith Allan Schneider) writes:
|> kmr4@po.CWRU.edu (Keith M. Ryan) writes:
|> 
|> >>Then why do people keep asking the same questions over and over?
|> >Because you rarely ever answer them.
|> 
|> Nope, I've answered each question posed, and most were answered multiple
|> times.

	He:   Fifty dollars if I can't answer your question.

	She:  What is the Big Bang theory.

	He:   The Big Bang theory is a recipe for cookies.

	She:  Fifty dollars, please.

	He:   Hey, I didn't 

Number of words to replace:  3
- Input data:
 From: Jimi Hendrix (Dane Hendrix)
Subject: Processing stereophony stereo images
Reply-To: hendrix@oasys.dt.navy.mil (Dane Hendrix)
Organization: Code 1542, DTMB, Bethesda, MD
Lines: 16

I'm interested in find out what is involved in processing pairs of 
stereo photographs.  I have black-and-white photos and would like 
to obtain surface contours.

I'd prefer to do the processing on an SGI, but would be interested
in hearing what software/hardware is used for this type of
image processing.

Please email and/or post to comp.sys.sgi.graphics your responses.

Thanks,

Dane Hendrix                              | email: dane@wizard.dt.navy.mil 
DTMB (a.k.a. Headquarters, Carderock Div.,|  or hendrix@oasys.dt.navy.mil
Naval Surface Warfare Center)             |  or hendrix@nas.nasa.gov 
Code 1542, Bethesda, MD 20084-5000        | phone: (301)227-1340
  

- With Thesaurus:
 From: Jimi Hendrix (Dane Hendrix)
Subject: Processing stereophony stereo Ji

Number of words to replace:  3
- Input data:
 From: jmetz@austin.ibm.com capable rhenium Twitching eye?
Originator: jmetz@jmetz.austin.ibm.com
Organization: IBM Austin
Lines: 4


  I had this one time.  I attributed it to a lack of sleep since it disappeared
after a few nights of good zzz's.

  

- With Thesaurus:
 From: jmetz@austin.ibm.com capable rhenium Twitching middle jmetz@jmetz.austin.ibm.com
Organization: IBM Austin
Lines: 4


  I had this one time.  I attributed it to a lack of sleep since it disappeared
after a few nights of good zzz's.

   
998
Number of words to replace:  3
- Input data:
 From: "Robert Knowles" <p00261@psilink.com>
Subject: atomic diverting 75 Amusing atheists and agnostics
In-Reply-To: <timmbake.735261806@mcl>
Nntp-Posting-Host: 127.0.0.1
Organization: Kupajava, East of Krakatoa
X-Mailer: PSILink-DOS (3.3)
Lines: 18

>DATE:   19 Apr 93 23:23:26 GMT
>FROM:   Bake Timmons <timmbake@mcl.ucsb.edu>
>
>My my, there _are_ a few atheists with time on their hands.

We have got 2000 train examples. NB:

In [241]:
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', MultinomialNB()),
])
text_clf.fit(twenty_train.data, twenty_train.target)

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data
predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target) 

0.8501845018450185

Performance is 0.8501845018450185. It was 0.8383763837638376 with Thesaurus without geom.distribution. It's abou 1,2% improvement and even a bit better than NB on original 2000 train docs (0.8287822878228782)

And now SVM:

In [243]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='hinge', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.8516605166051661

Performance is  0.8516605166051661. With Thesaurus without geom.distribution it was 0.844280442804428. It's 0,7% improvement. Original data performance - 0.8605166051660517.

And Log Regression

In [244]:
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.8162361623616237

Performance is 0.8162361623616237. Thesaurus without geometrical distribution had 0,806642066420664 performance. On the original Datset it was 0,82140221402214.

In [ ]:
Performance of the Logistic Regression (with Stochastic Gradien Descent) on the original Dataset of 2000 documents:

In [6]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)

twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.8214022140221402

Result is 0.8214022140221402

On 100 documents:

In [16]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)

twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.6605166051660517

Result is 0.6605166051660517

On 200 documents:

In [17]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:200]
twenty_train.target = twenty_train.target[:200]

from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.7107011070110701

Result is 0.7107011070110701

On 300 documents:

In [18]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:300]
twenty_train.target = twenty_train.target[:300]

from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0.7623616236162362

Result is 0.7623616236162362

Now let's take 100 examples and augment them with back translation and test with Logistic Regression:

In [20]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


0.6678966789667896

Result is 0.6678966789667896

In [ ]:
And now let's augment 300 examples using back translation with "de" and "fr":

In [22]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

for i in range(len(twenty_train.data)):
    print(i)
    ger_transl = translate(twenty_train.data[i], "de")
    new = translate(ger_transl, "en")
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    fr_transl = translate(twenty_train.data[i], "fr")
    new1 = translate(fr_transl, "en")
    (twenty_train.data).append(new1)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)


0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


0.6523985239852399

Result is 0.6523985239852399

And now 200 with thesarius:

In [27]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

for i in range(len(twenty_train.data)):
    print(i)
    new = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


0.6730627306273063

Result is 0.6730627306273063

And now take 100 and make 200 with Thesaurus with geometrical distribution and use Lor Regression

In [246]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

for i in range(len(twenty_train.data)):
    print(i)
    new = thesaurus_right(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0
Number of words to replace:  5
- Input data:
 From: vdp@mayo.edu (Vinayak Dutt)
Subject: rhenium Islamic Banks (was rhenium Slavery
Reply-To: vdp@mayo.edu
Organization: mayonnaise Foundation/Mayo grad School :Rochester, MN
Lines: 39

In article 28833@monu6.cc.monash.edu.au,  darice@yoyo.cc.monash.edu.au (Fred Rice) writes:
#In <1993Apr14.143121.26376@bmw.mayo.edu> vdp@mayo.edu (Vinayak Dutt) writes:
#>So instead of calling it interest on deposits, you call it *returns on investements*
#>and instead of calling loans you call it *investing in business* (that is in other words
#>floating stocks in your company). 
#
#No, interest is different from a return on an investment.  For one
#thing, a return on an investment has greater risk, and not a set return
#(i.e. the amount of money you make can go up or down, or you might even
#lose money).  The difference is, the risk of loss is shared by the
#investor, rather than practically all the risk being taken by the
#borrower when the borrower b

Number of words to replace:  2
- Input data:
 From: med50003@nusunix1.nus.sg (WANSAICHEONG KHIN-LIN)
Subject: Ra MORBUS MENIERE - is there a real remedy?
Organization: National University of Singapore
X-Newsreader: TIN [version 1.1 PL6]
Lines: 21

It would be nice to think that individuals can somehow 'beat the system'
and like a space explorer, boldly go where no man has gone before and
return with a prize cure. Unfortunately, too often the prize is limited
and the efficacy of the 'cure' questionable when applied to all
sufferers.

This applies to both medical researchers and non-medical individuals.
Just because it appears in an obscure journal and may be of some use
does not make the next cure-all. What about the dozens of individuals
who have courageously participated in clinical trials? Did they have any
guarentee of cures? Are they any less because they didn't trumpet their
story all over the world?

As a parting note, wasn't there some studies done on Gingko seeds for
Meniere's?

Number of words to replace:  1
- Input data:
 From: halat@pooh.bears (Jim Halat)
Subject: Re: After 2000 years, can we say that Christian Morality is
Reply-To: halat@pooh.bears (Jim Halat)
Lines: 45

In article <1r3qab$o1v@horus.ap.mchp.sni.de>, frank@D012S658.uucp (Frank O'Dwyer) writes:
>In article <930421.102525.9Y9.rusnews.w165w@mantis.co.uk> mathew <mathew@mantis.co.uk> writes:
>#frank@D012S658.uucp (Frank O'Dwyer) writes:
>#> In article <930420.100544.6n0.rusnews.w165w@mantis.co.uk> mathew
>#> <mathew@mantis.co.uk> writes:
>#> #This is complete nonsense.  Relativism means saying that there is no absolut
>#> #standard of morality; it does NOT mean saying that all standards of morality
>#> #are equally good.
>#> 
>#> Presumably this means that some moral systems are better than others?
>#> How so?  How do you manage this without an objective frame of reference?
>#

Either Frank O'Dwyer or mathew said:

[...stiff deleted...]

>#Which goes faster, a bullet or a snail?  How come you c

Number of words to replace:  1
- Input data:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: Re: Yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg


- With Thesaurus:
 From: jaeger@buphy.bu.edu (Gregg Jaeger)
Subject: rhenium Yet more Rushdie [Re: ISLAMIC LAW]
Organization: Boston University Physics Department
Lines: 14

In article <1qi3l5$jkj@fido.asd.sgi.com> livesey@solntze.wpd.sgi.com (Jon Livesey) writes:

>I hope an Islamic Bank is something other than BCCI, which
>ripped off so many small depositors among the Muslim
>community in the Uk and elsewhere.

>jon.

Grow up, childish propagandist.




Gregg
 
10
Number of words to replace:  2
- Input

Number of words to replace:  3
- Input data:
 From: ds0007@medtronic.COM (Dale meter Skiba)
Subject: Ra JUDAS, CRUCIFIXION, TYRE, Etc...
Nntp-Posting-Host: bass.pace.medtronic.com
Organization: Medtronic, Inc.
X-Newsreader: TIN [version 1.1 PL8]
Lines: 43

David Joslin (joslin@pogo.isp.pitt.edu) wrote:
: af664@yfn.ysu.edu (Frank DeCenso, Jr.) writes:
: >Based on the amount of E-Mail from fellow Christians who have read the
: >posts and told me I was wasting my time with Butler and Joslin, I told
: >them I wasn't doing it for DB or  DJ but for other Christians.  They
: >have told me that DB's and DJ's arguments won't convince most Bible
: >studying Christians.  So I have reevaluated my purpose here and it's
: >also contributed to my decision.

: So most Bible-studying Christians won't be convinced by my arguments? 
: And this is supposed to be a Good Thing, I presume?

Where does this "Most Bible studying Christians think as Frank
does" come from.  And what implied "good" are you doing 

...

Number of words to replace:  2
- Input data:
 From: irfan@davinci.ece.wisc.edu (Irfan Alan)
Subject: A TREATISE ON THE MIRACLES OF Elijah Muhammad SAW, PART-1
Organization: Univ. of Wisconsin-Madison; Electrical & Computer Engineering
Distribution: usa
Lines: 81

DROPLET VOL 1, No 11, Part 1

A  D R O P L E T
From The Vast Ocean Of The Miraculous Qur'an

Translations from the Arabic and Turkish Writings of 
Bediuzzaman Said Nursi, The Risale-i Noor

VOL 1, No 11, Part 1
------------------------------------------------------------------


   		 NINETEENTH LETTER  

		 MU'JIZAT-I AHMEDIYE RISALESI 
(A TREATISE ON THE MIRACLES OF MUHAMMAD SAW)       
(SAW: PEACE AND BLESSINGS BE UPON HIM)

In His Name (ALLAH) , Be He (ALLAH) Glorified!
There is Nothing But Glorifies His (ALLAH's) Praise.

In The Name Of  Allah, The Compassionate, The Merciful

   "He is who has sent His Messenger with
guidance and the religion of truth  to make it
supreme over all religion:  and sufficient is Allah
as a W

Number of words to replace:  2
- Input data:
 From: kjiv@lrc.edu
Subject: Hismanal, et. aluminium effects
Organization: Lenoir-Rhyne College, Hickory, NC
Lines: 22

Can someone tell me whether or not any of the following medications 
has been linked to rapid/excessive weight gain and/or a distorted 
sense of taste or smell:  Hismanal; Azmacort (a topical steroid to 
prevent asthma); Vancenase.

Also:
You may have guessed, I'm an allergy sufferer--but I'm beginning to 
suspect I'm also the victim of a Dr. toliberal with the prescription 
p. The allergist I went to last Oct. simply inquired about my symptons 
( I was suffering chronic asthma attacks), gave me a battery of 
allergy tests, and went down a checklist of drugs (a photocopied 
sheet).  I've gained out 30 lbs. since then though I haven't eaten 
more or much differently than before; I'vsuffered depression; , 
fatigue; and I've experienced a foul smell and sense of taste for 
about the last two months.  I mentioned the lack of sm

Number of words to replace:  1
- Input data:
 From: Mark-Tarbell@suite.com
Subject: Amniocentesis, et. al.
Organization: Suite Software
Lines: 7
Reply-To: suite!tarbell@uunet.uu.net
NNTP-Posting-Host: gilgamesh.suite.com

Is there some difference between the purposes behind
amniocentesis and chorionic villi sampling? They sound
similar to me, but are intended to detect different
things?

Thanks.



- With Thesaurus:
 From: Mark-Tarbell@suite.com
Subject: amnio et. al.
Organization: Suite Software
Lines: 7
Reply-To: suite!tarbell@uunet.uu.net
NNTP-Posting-Host: gilgamesh.suite.com

Is there some difference between the purposes behind
amniocentesis and chorionic villi sampling? They sound
similar to me, but are intended to detect different
things?

Thanks.

 
97
Number of words to replace:  1
- Input data:
 From: bil@okcforum.osrhe.edu (Bill Conner)
Subject: Re: [soc.motss, et al.] "Princeton axes matching funds for Boy Scouts"
Nntp-Posting-Host: okcforum.osrhe.edu
Organization: Okcfor

Number of words to replace:  2
- Input data:
 From: Joseph Mallord William Turner (Havok impersonated)
Subject: Re: Is MSG sensitivity superstition?
Article-I.D.: reed.1993Apr16.170752.6312
Organization: Reed College, Portland, OR
Lines: 35

In article <1qlgdrINN79b@gap.caltech.edu> carl@SOL1.GPS.CALTECH.EDU writes:
>In article <1993Apr15.173902.66278@cc.usu.edu>, slyx0@cc.usu.edu writes:
>=Surprise surprise, different people react differently to different things. One
>=slightly off the subject case in point. My brother got stung by a bee. I know
>=he is allergic to bee stings, but that his reaction is severe localized
>=swelling, not anaphylactic shock. I could not convince the doctors of that,
>=however, because that's not written in their little rule book.
>Of course, bee venom isn't a single chemical.  Could be your brother is
>reacting to a different component than the one that causes anaphylactic shock
>in other people.

Hmmm.  The last time I got stung by a bee I experienced the

0.6686346863468635

Performance is 0.6686346863468635. Thesaurus without geom. distribution had a performance of 0,667896678966789.

Take 1000 examples and make 2000 using Thesarius

In [28]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

for i in range(len(twenty_train.data)):
    print(i)
    new = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

0.8066420664206642

Result is 0.8066420664206642 (compare to original 0,82140221402214 performance with Logistc Regression)

Now Thesaurus with geometrical Distribution:

In [ ]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:1000]
twenty_train.target = twenty_train.target[:1000]

for i in range(len(twenty_train.data)):
    print(i)
    new = thesaurus_right(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

Result is ... It was 0.8066420664206642 with thesaurus without geometrical distribution(compare to original 0,82140221402214 performance with Logistc Regression)

Now take 100 original train documents and augment 300 using Thesarius and Back Translation:

In [76]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.pipeline import Pipeline
from mtranslate import translate

categories = ['alt.atheism', 'comp.graphics','sci.med','talk.religion.misc']

twenty_train = fetch_20newsgroups(subset='train',categories=categories, shuffle=True, random_state=42)
twenty_train.data = twenty_train.data[:100]
twenty_train.target = twenty_train.target[:100]

for i in range(len(twenty_train.data)):
    print(i)
    new = thesarius(twenty_train.data[i])
    (twenty_train.data).append(new)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    ger_transl = translate(twenty_train.data[i], "de")
    new1 = translate(ger_transl, "en")
    (twenty_train.data).append(new1)
    twenty_train.target = np.append(twenty_train.target, twenty_train.target[i])
    
from sklearn.linear_model import SGDClassifier
text_clf = Pipeline([('vect', CountVectorizer()),
('tfidf', TfidfTransformer()),
('clf', SGDClassifier(loss='log', penalty='l2',
alpha=1e-3, random_state=42,
max_iter=5, tol=None)),
])
text_clf.fit(twenty_train.data, twenty_train.target)  

import numpy as np
twenty_test = fetch_20newsgroups(subset='test',
categories=categories, shuffle=True, random_state=42)
docs_test = twenty_test.data

predicted = text_clf.predict(docs_test)
np.mean(predicted == twenty_test.target)

________________________________________________________________________________
Cache loading failed
________________________________________________________________________________



KeyboardInterrupt: 

Result is 0.659040590405904